# Défi EGC 2024 par Rayan Maniani et Bastien Hoorelbeke, `SCIA`

## Intrduction
Pour ce projet de Python pour le BigData, on se propose d'analyser l'influence du prix du Bitcoin sur le réseau de la blockchain, à savoir les corrélations qu'il peut y avoir entre le cours du Bitcoin et d'autres données propres au réseau. 

### import

In [22]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
from scripts.data_frame_generator import generate_external_time_series,generate_global_time_series, generate_blockchain_by_actor
from scripts.best_correlation import compute_best_correlation_by_col,display_comparison,display_correlation_histogram
from scripts.find import find_directory
import os
import plotly.express as px
import glob


## Récupération et prétraitement de de la donnée

In [38]:
SATOSH_PER_BTC = 1e-8
# Récupération des séries temporelles extérieures.
root_directory = os.getcwd()
timeseries_dir = 'timeseries'
dir_path = find_directory(root_directory, timeseries_dir)

In [39]:

external_df = generate_external_time_series(f"{dir_path}/external.csv")

# Récupération des données des 100 plus grands acteurs de la blockchain.
block_chain_by_actor_df_simple = generate_blockchain_by_actor(f'{dir_path}/blockchain_by_actor.csv')

# Récupération des données globales.
global_df = generate_global_time_series(f'{dir_path}/global.csv')

## Travail sur la donnée

### Première analyse: l'évolution du HashRate et du prix en dollars d'un Bitcoin
Faisons d'abord une première étude de l'évolution du prix du BTC et du HashRate, et cherchons à évaluer le niveau de corrélation entre leur évolution respective sur la période donnée.

In [25]:
import plotly.io as pio
pio.renderers
# Normalisation de la data frame
std_scaler = StandardScaler()
df1_normalized = std_scaler.fit_transform(external_df)
df1_normalized = pd.DataFrame(np.array(df1_normalized, dtype=np.float64), columns=external_df.columns,index=external_df.index)

# Lissage de la série temporelle
df_rolling = df1_normalized.rolling(window=7).mean()

# Création de la figure Plotly Express
fig = px.line(df_rolling,x=df_rolling.index,  y=["HashRate", "PriceUSD"],
              title="Evolution du HashRate et du prix du Bitcoin",
              labels={"value": "Valeur normalisée", "variable": "Variables", "Date": df_rolling.index.name},
              template="simple_white")

fig.show()

![alternative text](./pics/hash-rate-USD.png)

#### Evaluation des corrélations entre HashRate et le prix du Bitcoin en Dollars
En regardant les précédentes courbes affichées on peut remarquer que le HashRate et le prix en dollars augmentent de mannière comparable. Mesurons maintenant leur niveau de corrélation par la corrélation de Pearson.

In [26]:
correlation_matrix = external_df.corr()
correlation_coefficient = correlation_matrix.values[0,1]
print(f'Le coefficient de corrélation entre le HashRate et le prix en dollar du BTC est de {correlation_coefficient}')

Le coefficient de corrélation entre le HashRate et le prix en dollar du BTC est de 0.9374466899233475


On peut remarquer ici que le score de correlation de Pearson entre le PriceUSD et le HashRate est de 0.93, ce qui signifie que les PriceUSD et Hashrate on une relation linéaire qui est proche.

### Travail sur les 100 principaux acteurs de la blockcahin

Après avoir utilisé la corrélation de Pearson, on veut chercher ici à trouver des correlation sur l'évolution de chaque acteurs entre eux à savoir si deux acteurs ont une activité qui évolue de manière similaire comme il a été fait pour l'analyse du HashRate et du cours du Bitcoin.

On peut alors se poser la question si l'activité de certains groupes d'acteurs sont corrélées entre elles selon un certain critère tel que les transaction émises (`spent`) ou encore les frais payés (`sum_fee`).

On étudie dans la cellule ci-dessous le couple d'acteurs qui ont une évolution de leur montant reçu la plus proche. 

In [27]:
# Nom de la colonne à analyser dans le block_chain_by_actor_df_simple
column_to_analyze = 'received'
# Appel d'une fonction déterminant le couple d'acteurs ayant le meilleur coefficient de corrélation 
max_index,max_col, max_value = compute_best_correlation_by_col(block_chain_by_actor_df_simple,column_to_analyze)
print(f"La valeur maximale de corrélation est {max_value} , les acteurs '{max_index}' et '{max_col}' ont leur évolution de '{column_to_analyze}' fortement corrélée.")

La valeur maximale de corrélation est 0.9021413876901954 , les acteurs 'BTCC.com' et 'BtcTrade.com' ont leur évolution de 'received' fortement corrélée.


In [28]:
column_to_analyze = 'received'
max_index, max_col, max_value = compute_best_correlation_by_col(block_chain_by_actor_df_simple, column_to_analyze)

display_comparison(block_chain_by_actor_df_simple,max_col,max_index,column_to_analyze,10)

![alternative text](./pics/BTCC.png)

On remarque une augmentation du nombre de transactions vers avril 2016 ainsi qu'une baisse vers juillet dans les deux courbes. On notera que le nombre de transactions n'est pas du même ordre de grandeur. C'est ici un exemple de corrélation entre deux acteurs selon un critère fixé en l'occurence le volume reçu. Voyons maintenant si les acteurs suivent une tendance commune sur un critère particulier.

Cela ne montre pas la corrélation du cours du Bitcoin sur le comportement des 100 plus grands acteurs. Il s'agit d'un simple exemple de corréaltion de deux acteurs selon un critère donné (`received`) qui va nous permettre de comprendre la suite de 'étude.

#### Pondération des Satoshis avec l'évolution du prix en dollars. 
Afin d'avoir une vision plus globale sur les données des acteurs ainsi que les données externes (`PriceUSD` qui nous intéresse pour cette étude), on décide de convertir les données initialement en Satoshis en Dollars ,telles que `sent`, `received` et `sum_fee`. 

In [29]:
block_chain_by_actor_df = block_chain_by_actor_df_simple.copy()
block_chain_by_actor_df['spentUSD'] =  block_chain_by_actor_df['spent']*SATOSH_PER_BTC*external_df['PriceUSD']
block_chain_by_actor_df['receivedUSD'] =  block_chain_by_actor_df['received']*SATOSH_PER_BTC*external_df['PriceUSD']
block_chain_by_actor_df['sum_feeUSD'] =  block_chain_by_actor_df['sum_fee']*SATOSH_PER_BTC*external_df['PriceUSD']
pd.read_csv('generated_data/pretty_block_chain_by_actor.csv',index_col='date')

identity      received  nb_received  \
date                                                                      
2015-01-01                    HappyCoins.com  1.377590e+09          4.0   
2015-01-01                               269  7.323854e+08        190.0   
2015-01-01                          Bter.com  4.232779e+10        338.0   
2015-01-01                  BitBargain.co.uk  4.153552e+09         25.0   
2015-01-01                          72472408  4.213276e+08          6.0   
...                                      ...           ...          ...   
2017-06-30                        BTCJam.com  1.188544e+06          2.0   
2017-06-30                               417  1.269886e+11        935.0   
2017-06-30  CoinTrader.net_LocalBitcoins.com  5.399136e+10        665.0   
2017-06-30            ePay.info_CoinJoinMess  4.317324e+10       2438.0   
2017-06-30                              1226  2.819778e+08         21.0   

               sum_fee  mean_fee_for100  nb_transactions          sent  \
date                                                                     
2015-01-01     49596.0         0.004957              4.0  1.277500e+09   
2015-01-01    770000.0         0.260248             60.0  1.087653e+09   
2015-01-01   1070000.0         0.390202             70.0  7.314074e+10   
2015-01-01    140000.0         0.095593             16.0  6.111821e+09   
2015-01-01     60000.0         0.027924              6.0  5.216480e+08   
...                ...              ...              ...           ...   
2017-06-30    145053.0        10.876816              1.0  1.043491e+06   
2017-06-30   3197160.0         0.003197              2.0  1.000000e+11   
2017-06-30  12474795.0         0.268176              9.0  4.164831e+10   
2017-06-30  18664735.0         2.327340            277.0  1.449515e+11   
2017-06-30    302700.0         0.349447              6.0  3.296741e+08   

              self_spent  self_spent_estimated  nb_spent         spent  \
date                                                                     
2015-01-01  0.000000e+00          0.000000e+00       8.0  1.277500e+09   
2015-01-01  0.000000e+00          0.000000e+00     120.0  1.087653e+09   
2015-01-01  1.921924e+10          1.921924e+10     148.0  5.392150e+10   
2015-01-01  1.372861e+09          1.372861e+09      33.0  4.738960e+09   
2015-01-01  0.000000e+00          0.000000e+00      12.0  5.216480e+08   
...                  ...                   ...       ...           ...   
2017-06-30  0.000000e+00          0.000000e+00       2.0  1.043491e+06   
2017-06-30  0.000000e+00          1.000000e+11       2.0  0.000000e+00   
2017-06-30  3.001722e+09          3.001722e+09      58.0  3.864659e+10   
2017-06-30  1.205214e+11          1.205214e+11    4930.0  2.443010e+10   
2017-06-30  0.000000e+00          0.000000e+00      12.0  3.296741e+08   

                 spentUSD   receivedUSD  sum_feeUSD  
date                                                 
2015-01-01            NaN           NaN         NaN  
2015-01-01            NaN           NaN         NaN  
2015-01-01            NaN           NaN         NaN  
2015-01-01            NaN           NaN         NaN  
2015-01-01            NaN           NaN         NaN  
...                   ...           ...         ...  
2017-06-30      25.593830  2.915156e+01    3.557732  
2017-06-30       0.000000  3.114666e+06   78.417129  
2017-06-30  947889.453418  1.324253e+06  305.970802  
2017-06-30  599199.921181  1.058915e+06  457.792207  
2017-06-30    8085.957061  6.916104e+03    7.424359  

[90403 rows x 14 columns]

#### Affichage des données corrélées

Une fois les prix en Satoshis convertis en Dollars, on décide de créer une data frame, qui pour chaque couple d'acteurs et chaque critère va mesurer leur niveau de corrélation.

In [30]:
from scripts.best_correlation import best_correlation_df
best_corr_df = best_correlation_df(block_chain_by_actor_df,0)
best_corr_df = best_corr_df.sort_values('correlation_rate',ascending=False)
best_corr_df.head()

actor1           actor2  correlation_rate related_col
54016             107         69697250          0.957747  sum_feeUSD
58003      Bitcoin.de   CoinMotion.com          0.950021  sum_feeUSD
58078    Bitstamp.net  CoinSpot.com.au          0.946132  sum_feeUSD
58287  CoinMotion.com      Paymium.com          0.941566  sum_feeUSD
54048             107    CoinGaming.io          0.940180  sum_feeUSD

* `actor1`, `actor2` : couples d'acteurs
* `correlation_rate` :  niveau de corrélation entre les deux acteurs
* `related_col` : critère de corrélation

In [31]:
display_comparison(block_chain_by_actor_df,'Bitcoin.de','CoinMotion.com','sum_fee',7)
display_comparison(block_chain_by_actor_df,'Bitstamp.net','CoinSpot.com.au','sum_feeUSD',7)

On remarque ici que pour ces deux couples, leur évolution de `sum_feeUSD` sont très proches.

On va chercher ici à afficher pour chaque critère un histogramme de la répartition des coefficients de corrélation des 4950 couples d'acteurs.

In [32]:
display_correlation_histogram(best_corr_df)

![alternative text](./pics/hists.png)

On fait ensuite un bilan statistique de chaque critère.

In [33]:
best_corr_df.groupby(by='related_col').describe()

correlation_rate                                          \
                                count      mean       std       min       25%   
related_col                                                                     
mean_fee_for100                4950.0  0.196197  0.236202 -0.611723  0.010631   
nb_received                    4950.0  0.075358  0.292866 -0.849307 -0.097909   
nb_spent                       4950.0  0.058878  0.290211 -0.812685 -0.118068   
nb_transactions                4950.0  0.058991  0.277801 -0.833563 -0.103115   
received                       4950.0  0.029110  0.177611 -0.578405 -0.064122   
receivedUSD                    4950.0  0.147743  0.264193 -0.654974 -0.035437   
self_spent                     1128.0  0.003503  0.106009 -0.383264 -0.054574   
self_spent_estimated           3159.0  0.023699  0.114092 -0.508883 -0.030021   
sent                           4950.0  0.024422  0.162944 -0.525265 -0.065025   
spent                          4950.0  0.028072  0.165333 -0.651891 -0.059007   
spentUSD                       4950.0  0.119954  0.236577 -0.538261 -0.035379   
sum_fee                        4950.0  0.299640  0.304119 -0.583018  0.069362   
sum_feeUSD                     4950.0  0.515769  0.288079 -0.231344  0.336601   

                                                    
                           50%       75%       max  
related_col                                         
mean_fee_for100       0.173601  0.356446  0.883442  
nb_received           0.049711  0.241096  0.918101  
nb_spent              0.042203  0.241723  0.927626  
nb_transactions       0.045230  0.219023  0.902752  
received              0.013424  0.110745  0.902141  
receivedUSD           0.078918  0.313264  0.897676  
self_spent           -0.005548  0.052008  0.541617  
self_spent_estimated -0.003063  0.060914  0.626191  
sent                  0.008328  0.104326  0.895337  
spent                 0.016119  0.109532  0.841254  
spentUSD              0.061773  0.260904  0.914727  
sum_fee               0.329646  0.539893  0.917397  
sum_feeUSD            0.588523  0.741837  0.957747

* On a obtenu les distributions des corrélations entre chaque couple d'acteurs ci-dessus. La distibution de `sum_feeUSD` est centrée en 0.5 ce qui montre que la somme des frais envoyés en dollars par les acteurs suit une certaine tendance. 
* La majorité des autres distributions se centrent en 0 et l'ensemble des valeurs est principalement distribué sur l'intervalle [-0.5,0.5 ] ce qui montre une très faible corrélation et donc que les acteurs évoluent plus de manière indépendante.

## Bilan des observations
* On remarque donc que le cours du Bitcoin et le comportement des acteurs vis-a-vis des frais en Dollars sont corrélés, c'est à dire que les frais des transaction payés par les acteurs en dollars suivent une tendance similaire. 
* Le HashRate et le cours du Bitcoin sont également corrélés. 

## Analyse et conclusion des observations
**"Corrélation n'est pas causalité"** 

Ces corrélations ne suffisent pas à expliquer le phénomène sous-jacent. 

En général lorsque le prix du Bitcoin augmente, les frais de transaction exprimés en dollars ont également tendance à augmenter. De même, lorsque le prix du Bitcoin baisse, les frais de transaction exprimés en dollars ont également tendance à diminuer.

Cela est dû au fait que les frais de transaction Bitcoin sont généralement exprimés en satoshis par octet (sat/B), une unité relative au montant de Bitcoin envoyé et à la taille de la transaction en octets. Ainsi, lorsque le prix du Bitcoin augmente, les frais de transaction en satoshis peuvent rester relativement stables, mais leur valeur en dollars augmentera.

Cependant, il convient de noter que la corrélation entre le prix du Bitcoin et les frais de transaction exprimés en dollars peut varier en fonction de facteurs externes tels que la concurrence entre les mineurs, la taille des blocs, la congestion du réseau et la demande pour l'utilisation du réseau. Par conséquent, il est important de considérer ces facteurs lors de l'évaluation de la corrélation entre le prix du Bitcoin et les frais de transaction exprimés en dollars.

# Début d'etude sur les réseaux et les 100 acteurs (Non terminé)
Dans cette étude on cherche à déterminer les similtudes entre les acteurs en termes de transactions, à savoir si les acteurs qui suivent la même tendance sur les frais en dollars on des habitudes de transaction communes.

In [34]:
closest_actors = best_corr_df[(best_corr_df['related_col']=='sum_feeUSD') & (best_corr_df['correlation_rate']>=0.9)]
noms_uniques_actor1 = closest_actors["actor1"].unique()
noms_uniques_actor2 = closest_actors["actor2"].unique()
actors_list = pd.Series(list(noms_uniques_actor1) + list(noms_uniques_actor2))
actors_list = actors_list.unique()
actors_list


array(['107', 'Bitcoin.de', 'Bitstamp.net', 'CoinMotion.com', '69697250',
       '1070', '289', 'BitBargain.co.uk', '292', '101', 'CoinJar.com',
       '898', '7277', 'HappyCoins.com', '523', 'MercadoBitcoin.com.br',
       'HaoBTC.com', 'CoinGaming.io', 'BTC-e.com', '35', '269', '227',
       '419', 'PocketDice.io', 'CoinSpot.com.au', 'Paymium.com',
       'Xapo.com', 'FYBSG.com', 'SatoshiMines.com', 'SimpleCoin.cz',
       'SafeDice.com', '821', 'Matbea.com', 'Poloniex.com', '61'],
      dtype=object)

In [35]:
def get_and_filter(file_path:str, actor_list)-> pd.DataFrame:
    """
    Renvoie la liste des transaction de l'ensemble des acteurs dans `actor_list`.
    """
    df = pd.read_csv(file_path)
    return df [(df['Source'].isin(actor_list)) & df['Target'].isin(actor_list)]

def join_networks_df(df1: pd.DataFrame ,df2: pd.DataFrame) -> pd.DataFrame:
    """
    Joint deux dataframes issues du dossier networks.
    """
    df = pd.merge(df1, df2, on=['Source', 'Target'], how='outer', suffixes=('_1', '_2'))
    df['value'] = df['value_1'].fillna(0) + df['value_2'].fillna(0)
    df['nb_transactions'] = df['nb_transactions_1'].fillna(0) + df['nb_transactions_2'].fillna(0)
    df = df.drop(columns=['value_1', 'value_2','nb_transactions_1','nb_transactions_2'])
    return df

def generate_network_dataframe(actors_list,file_pattern:str ='./networks/*.csv' ) -> pd.DataFrame:
    files_list = glob.glob(file_pattern)
    df = get_and_filter(files_list[0],actors_list)
    for file in files_list[1:]:
        cur_df = get_and_filter(file,actors_list)
        df = join_networks_df(df,cur_df)
    return df

In [36]:
network_df = generate_network_dataframe(block_chain_by_actor_df.identity.unique())
network_df.to_csv('generated_data/network.csv')

In [37]:
network_df

Source              Target         value  \
0                        396           Huobi.com  1.515598e+13   
1     ePay.info_CoinJoinMess                 175  1.397186e+12   
2     ePay.info_CoinJoinMess                 122  3.537344e+12   
3     ePay.info_CoinJoinMess       PocketDice.io  1.199426e+11   
4                   BX.in.th        Poloniex.com  6.686717e+12   
...                      ...                 ...           ...   
4264        SatoshiMines.com          BitcoinFog  4.185632e+07   
4265                     417  TheRockTrading.com  1.061400e+09   
4266             Paymium.com            BTCC.com  1.481168e+10   
4267      TheRockTrading.com     FortuneJack.com  3.421432e+06   
4268                70063369                 417  7.910387e+06   

      nb_transactions  
0              4557.0  
1               957.0  
2              1067.0  
3              1485.0  
4              8718.0  
...               ...  
4264              1.0  
4265              1.0  
4266              1.0  
4267              1.0  
4268              1.0  

[4269 rows x 4 columns]